<center><h1> Comparative performance of double DQN, dueling DQN and prioritised DQN for solving Lunar Lander problem </h1></center>

## Ziad Al-Ziadi and Behzad Javaheri

### Task 4 Deep Reinforcement Learning

In this task we will compare the performance of 3 reinforcement learning model free and off-policy algorithms in solving Lunar Lander problem using LunadLander-v2 OpenAI gym environment. We have selected Double DQN, Dueling DQN and Prioritised DQN that have reportedly improved upon the performance of DQN. We will briefly describe these models before implementation.

1. Double DQN algorithm: This algorithm is an improvement over the original DQN algorithm in particular attempting to address the overestimation of true reward for an action. It suggests that a particular action will lead to a reward that is higher than what the agent will obtain in reality. Hasselt et al., (2016) suggested Double DQN algorithm as a means to overcome this shortcoming. Double DQN utilises the same two network architecture observed in DQN with modification to its implementation.  This is primarily achieved by decoupling the action selection from evaluation. Double DQN uses local network to select action for the next state with the target network providing the Q values. The authors prposed a modification to the Bellman equation as demonstrated below:

Modified Bellman equation proposed by Hassels et al., (2016): https://arxiv.org/abs/1509.06461


2. Dueling DQN

3. Prioritised DQN

#### 1. Importing required libraries

In [25]:
import math, random

import gym
import numpy as np

import torch as T
import torch.nn as nn
import torch.optim as optim
import torch.autograd as autograd 
import torch.nn.functional as F

from IPython.display import clear_output, set_matplotlib_formats, display
import matplotlib.pyplot as plt
from matplotlib import animation
import matplotlib as mpl
import seaborn as sns
from IPython.display import display
%matplotlib inline
import plotly.io as pio
set_matplotlib_formats('retina')
pio.renderers.default='notebook'
mpl.rcParams['figure.dpi'] = 300

from collections import deque

import warnings
warnings.simplefilter("ignore")
warnings.filterwarnings('ignore')
def ignore_warn(*args, **kwargs):
    pass
warnings.warn = ignore_warn

utilise_cuda = T.cuda.is_available()
Variable = lambda *args, **kwargs: autograd.Variable(*args, **kwargs).cuda() if utilise_cuda else autograd.Variable(*args, **kwargs)

#### 2.Replay Buffer

Q learning is an off-policy method. In off-policy methods we often save samples and then train on them. DDQN has a memory buffer that stores state, action, reward, terminal condition, and next state samples. In the training loop, DDQN will sample from this memory buffer and train on the saved samples. The replay buffer is essentially a queue that we randomly sample from. When the queue gets full we replace the first element of the queue.

In [26]:
# Replay buffer for double DQN
class ReplayBuffer_doubledqn(object):
    def __init__(self, capacity):
        self.buffer = deque(maxlen=capacity)
    
    def push(self, state_doubledqn, action_doubledqn, reward_doubledqn, next_state_doubledqn, terminal):
        state_doubledqn      = np.expand_dims(state_doubledqn, 0)
        next_state_doubledqn = np.expand_dims(next_state_doubledqn, 0)
            
        self.buffer.append((state_doubledqn, action_doubledqn, reward_doubledqn, next_state_doubledqn, terminal))
    
    def sample(self, batch_size):
        state_doubledqn, action_doubledqn, reward_doubledqn, next_state_doubledqn, terminal = zip(*random.sample(self.buffer, batch_size))
        return np.concatenate(state_doubledqn), action_doubledqn, reward_doubledqn, np.concatenate(next_state_doubledqn), terminal
    
    def __len__(self):
        return len(self.buffer)

# Replay buffer for dueling DQN
class ReplayBuffer_dueling(object):
    def __init__(self, capacity):
        self.buffer = deque(maxlen=capacity)
    
    def push(self, state_dueling, action_dueling, reward_dueling, next_state_dueling, terminal):
        state_dueling      = np.expand_dims(state_dueling, 0)
        next_state_dueling = np.expand_dims(next_state_dueling, 0)
            
        self.buffer.append((state_dueling, action_dueling, reward_dueling, next_state_dueling, terminal))
    
    def sample(self, batch_size):
        state_dueling, action_dueling, reward_dueling, next_state_dueling, terminal = zip(*random.sample(self.buffer, batch_size))
        return np.concatenate(state_dueling), action_dueling, reward_dueling, np.concatenate(next_state_dueling), terminal
    
    def __len__(self):
        return len(self.buffer)

# Replay buffer for prioritized DQN    
class NaivePrioritizedBuffer_prioritised(object):
    def __init__(self, capacity, prob_alpha=0.6):
        self.prob_alpha = prob_alpha
        self.capacity   = capacity
        self.buffer     = []
        self.pos        = 0
        self.priorities = np.zeros((capacity,), dtype=np.float32)
    
    def push(self, state_prioritised, action_prioritised, reward_prioritised, next_state_prioritised, terminal):
        assert state_prioritised.ndim == next_state_prioritised.ndim
        state_prioritised      = np.expand_dims(state_prioritised, 0)
        next_state_prioritised = np.expand_dims(next_state_prioritised, 0)
        
        max_prio = self.priorities.max() if self.buffer else 1.0
        
        if len(self.buffer) < self.capacity:
            self.buffer.append((state_prioritised, action_prioritised, reward_prioritised, next_state_prioritised, terminal))
        else:
            self.buffer[self.pos] = (state_prioritised, action_prioritised, reward_prioritised, next_state_prioritised, terminal)
        
        self.priorities[self.pos] = max_prio
        self.pos = (self.pos + 1) % self.capacity
    
    def sample(self, batch_size, beta=0.4):
        if len(self.buffer) == self.capacity:
            prios = self.priorities
        else:
            prios = self.priorities[:self.pos]
        
        probs  = prios ** self.prob_alpha
        probs /= probs.sum()
        
        indices = np.random.choice(len(self.buffer), batch_size, p=probs)
        samples = [self.buffer[idx] for idx in indices]
        
        total    = len(self.buffer)
        weights  = (total * probs[indices]) ** (-beta)
        weights /= weights.max()
        weights  = np.array(weights, dtype=np.float32)
        
        batch       = list(zip(*samples))
        states_prioritised      = np.concatenate(batch[0])
        actions_prioritised     = batch[1]
        rewards_prioritised     = batch[2]
        next_states_prioritised = np.concatenate(batch[3])
        terminals       = batch[4]
        
        return states_prioritised, actions_prioritised, rewards_prioritised, next_states_prioritised, terminals, indices, weights
    
    def update_priorities(self, batch_indices, batch_priorities):
        for idx, prio in zip(batch_indices, batch_priorities):
            self.priorities[idx] = prio

    def __len__(self):
        return len(self.buffer)


#### Lunar lander discrete environment

In [27]:
env_id = "LunarLander-v2"
env = gym.make(env_id)

#### Epsilon greedy search

In [28]:
beta_start = 0.4
beta_frames = 1000 
beta_by_frame = lambda update_interval: min(1.0, beta_start + update_interval * (1.0 - beta_start) / beta_frames)


epsilon_start = 1.0
epsilon_final = 0.01
epsilon_decay = 500

epsilon_by_frame_doubledqn = lambda update_interval: epsilon_final + (epsilon_start - epsilon_final) * math.exp(-1. * update_interval / epsilon_decay)
epsilon_by_frame_dueling = lambda update_interval: epsilon_final + (epsilon_start - epsilon_final) * math.exp(-1. * update_interval / epsilon_decay)
epsilon_by_frame_prioritised = lambda update_interval: epsilon_final + (epsilon_start - epsilon_final) * math.exp(-1. * update_interval / epsilon_decay)

#### Defining double DQN, dueling DQN and prioritised DQN network

In [29]:
class DQN(nn.Module):
    def __init__(self, num_inputs, num_actions):
        super(DQN, self).__init__()
        
        self.layers = nn.Sequential(
            nn.Linear(env.observation_space.shape[0], 128),
            nn.ReLU(),
            nn.Linear(128, 128),
            nn.ReLU(),
            nn.Linear(128, env.action_space.n)
        )
        
    def forward(self, x):
        return self.layers(x)
    
    def act(self, state_doubledqn, epsilon_doubledqn):
        if random.random() > epsilon_doubledqn:
            state_doubledqn   = Variable(T.FloatTensor(state_doubledqn).unsqueeze(0), volatile=True)
            q_value = self.forward(state_doubledqn)
            action_doubledqn = q_value.max(1)[1].item()
        else:
            action_doubledqn = random.randrange(env.action_space.n)
        return action_doubledqn
    
    
class DuelingDQN(nn.Module):
    def __init__(self, num_inputs, num_outputs):
        super(DuelingDQN, self).__init__()
        
        self.feature = nn.Sequential(
            nn.Linear(num_inputs, 128),
            nn.ReLU()
        )
        
        self.advantage = nn.Sequential(
            nn.Linear(128, 128),
            nn.ReLU(),
            nn.Linear(128, num_outputs)
        )
        
        self.value = nn.Sequential(
            nn.Linear(128, 128),
            nn.ReLU(),
            nn.Linear(128, 1)
        )
        
    def forward(self, x):
        x = self.feature(x)
        advantage = self.advantage(x)
        value     = self.value(x)
        return value + advantage  - advantage.mean()
    
    def act(self, state_dueling, epsilon_dueling):
        if random.random() > epsilon_dueling:
            state_dueling   = Variable(T.FloatTensor(state_dueling).unsqueeze(0), volatile=True)
            q_value = self.forward(state_dueling)
            action_dueling = q_value.max(1)[1].item()
        else:
            action_dueling = random.randrange(env.action_space.n)
        return action_dueling

class PrioritisedDQN(nn.Module):
    def __init__(self, num_inputs, num_actions):
        super(PrioritisedDQN, self).__init__()
        
        self.layers = nn.Sequential(
            nn.Linear(env.observation_space.shape[0], 128),
            nn.ReLU(),
            nn.Linear(128, 128),
            nn.ReLU(),
            nn.Linear(128, env.action_space.n)
        )
        
    def forward(self, x):
        return self.layers(x)
    
    def act(self, state_prioritised, epsilon_prioritised):
        if random.random() > epsilon_prioritised:
            state_prioritised   = Variable(T.FloatTensor(state_prioritised).unsqueeze(0), volatile=True)
            q_value = self.forward(state_prioritised)
            action_prioritised  = q_value.max(1)[1].item()
        else:
            action_prioritised = random.randrange(env.action_space.n)
        return action_prioritised

In [30]:
# Double DQN
current_model_doubledqn = DQN(env.observation_space.shape[0], env.action_space.n)
target_model_doubledqn  = DQN(env.observation_space.shape[0], env.action_space.n)

if utilise_cuda:
    current_model_doubledqn = current_model_doubledqn.cuda()
    target_model_doubledqn  = target_model_doubledqn.cuda()
    
optimizer_doubledqn = optim.Adam(current_model_doubledqn.parameters())

replay_buffer_doubledqn = ReplayBuffer_doubledqn(1000)

# Dueling DQN
current_model_dueling = DuelingDQN(env.observation_space.shape[0], env.action_space.n)
target_model_dueling  = DuelingDQN(env.observation_space.shape[0], env.action_space.n)

if utilise_cuda:
    current_model_dueling = current_model_dueling.cuda()
    target_model_dueling  = target_model_dueling.cuda()
    
optimizer_dueling = optim.Adam(current_model_dueling.parameters())

replay_buffer_dueling = ReplayBuffer_dueling(1000)

# Prioritised DQN
current_model_prioritised = PrioritisedDQN(env.observation_space.shape[0], env.action_space.n)
target_model_prioritised  = PrioritisedDQN(env.observation_space.shape[0], env.action_space.n)

if utilise_cuda:
    current_model_prioritised = current_model_prioritised.cuda()
    target_model_prioritised  = target_model_prioritised.cuda()
    
optimizer_prioritised = optim.Adam(current_model_prioritised.parameters())

replay_buffer_prioritised = NaivePrioritizedBuffer_prioritised(100000)

#### Synchronise policy and target net

In [31]:
def update_target_doubledqn(current_model_doubledqn, target_model_doubledqn):
    target_model_doubledqn.load_state_dict(current_model_doubledqn.state_dict())

def update_target_dueling(current_model_dueling, target_model_dueling):
    target_model_dueling.load_state_dict(current_model_dueling.state_dict())
    
def update_target_prioritised(current_model_prioritised, target_model_prioritised):
    target_model_prioritised.load_state_dict(current_model_prioritised.state_dict())
    
update_target_doubledqn(current_model_doubledqn, target_model_doubledqn)
update_target_dueling(current_model_dueling, target_model_dueling)
update_target_prioritised(current_model_prioritised, target_model_prioritised)

#### Calculating temporal difference loss for each network

In [32]:
def td_loss_doubledqn(batch_size):
    state_doubledqn, action_doubledqn, reward_doubledqn, next_state_doubledqn, terminal = replay_buffer_doubledqn.sample(batch_size)

    state_doubledqn      = Variable(T.FloatTensor(np.float32(state_doubledqn)))
    next_state_doubledqn = Variable(T.FloatTensor(np.float32(next_state_doubledqn)))
    action_doubledqn     = Variable(T.LongTensor(action_doubledqn))
    reward_doubledqn     = Variable(T.FloatTensor(reward_doubledqn))
    terminal       = Variable(T.FloatTensor(terminal))

    q_values      = current_model_doubledqn(state_doubledqn)
    next_q_values = current_model_doubledqn(next_state_doubledqn)
    next_q_state_values = target_model_doubledqn(next_state_doubledqn) 

    q_value       = q_values.gather(1, action_doubledqn.unsqueeze(1)).squeeze(1) 
    next_q_value = next_q_state_values.gather(1, T.max(next_q_values, 1)[1].unsqueeze(1)).squeeze(1)
    expected_q_value = reward_doubledqn + gamma * next_q_value * (1 - terminal)
    
    loss_doubledqn = (q_value - Variable(expected_q_value.data)).pow(2).mean()
        
    optimizer_doubledqn.zero_grad()
    loss_doubledqn.backward()
    optimizer_doubledqn.step()
    
    return loss_doubledqn


def td_loss_dueling(batch_size):
    state_dueling, action_dueling, reward_dueling, next_state_dueling, terminal = replay_buffer_dueling.sample(batch_size)

    state_dueling      = Variable(T.FloatTensor(np.float32(state_dueling)))
    next_state_dueling = Variable(T.FloatTensor(np.float32(next_state_dueling)))
    action_dueling     = Variable(T.LongTensor(action_dueling))
    reward_dueling     = Variable(T.FloatTensor(reward_dueling))
    terminal       = Variable(T.FloatTensor(terminal))

    q_values      = current_model_dueling(state_dueling)
    next_q_values = target_model_dueling(next_state_dueling)

    q_value          = q_values.gather(1, action_dueling.unsqueeze(1)).squeeze(1)
    next_q_value     = next_q_values.max(1)[0]
    expected_q_value = reward_dueling + gamma * next_q_value * (1 - terminal)
    
    loss_dueling = (q_value - expected_q_value.detach()).pow(2).mean()
        
    optimizer_dueling.zero_grad()
    loss_dueling.backward()
    optimizer_dueling.step()
    
    return loss_dueling


def td_loss_prioritised(batch_size, beta):
    state_prioritised, action_prioritised, reward_prioritised, next_state_prioritised, terminal, indices, weights = replay_buffer_prioritised.sample(batch_size, beta) 

    state_prioritised      = Variable(T.FloatTensor(np.float32(state_prioritised)))
    next_state_prioritised = Variable(T.FloatTensor(np.float32(next_state_prioritised)))
    action_prioritised     = Variable(T.LongTensor(action_prioritised))
    reward_prioritised     = Variable(T.FloatTensor(reward_prioritised))
    terminal       = Variable(T.FloatTensor(terminal))
    weights    = Variable(T.FloatTensor(weights))

    q_values      = current_model_prioritised(state_prioritised)
    next_q_values = target_model_prioritised(next_state_prioritised)

    q_value          = q_values.gather(1, action_prioritised.unsqueeze(1)).squeeze(1)
    next_q_value     = next_q_values.max(1)[0]
    expected_q_value = reward_prioritised + gamma * next_q_value * (1 - terminal)
    
    loss_prioritised  = (q_value - expected_q_value.detach()).pow(2) * weights
    prios = loss_prioritised + 1e-5
    loss_prioritised  = loss_prioritised.mean()
        
    optimizer_prioritised.zero_grad()
    loss_prioritised.backward()
    replay_buffer_prioritised.update_priorities(indices, prios.data.cpu().numpy())
    optimizer_prioritised.step()
    
    return loss_prioritised

#### Creating plotting function

In [1]:
def plot_dynamic(update_interval, rewards, losses):
    clear_output(True)
    plt.style.use('seaborn-dark-palette')
    mpl.rcParams['xtick.labelsize'] = 22
    plt.figure(figsize=(40,20))
    plt.subplot(321)
    plt.title('Double DQN: in frame %s, the reward is %s' % (update_interval, np.mean(all_rewards_doubledqn[-10:])), size=22, weight="bold")
    #plt.xlabel('Episode', size=22, weight="bold");
    plt.ylabel('Reward (Double DQN)', size=22, weight="bold");
    plt.xticks(size=20)
    plt.yticks(size=20)
    plt.ylim(-400, 150)
    #plt.grid(b=None)
    plt.plot(all_rewards_doubledqn, marker='o', linewidth=5, color='#2CBDFE')
    plt.subplot(322)
    plt.title('Double DQN: loss in comparable frames ', size=22, weight="bold")
    #plt.xlabel('Episode', size=22, weight="bold");
    plt.ylabel('Loss (Double DQN)', size=22, weight="bold");
    plt.xticks(size=20)
    plt.yticks(size=20)
    plt.ylim(0, 1200)
    plt.plot(losses_doubledqn, linewidth=3, color='#9D2EC5')
    plt.subplot(323)
    plt.title('Dueling DQN: in frame %s, the reward is %s' % (update_interval, np.mean(all_rewards_dueling[-10:])), size=22, weight="bold")
    #plt.xlabel('Episode', size=22, weight="bold");
    plt.ylabel('Reward (Dueling DQN)', size=22, weight="bold");
    plt.xticks(size=20)
    plt.yticks(size=20)
    plt.ylim(-400, 150)
    #plt.grid(b=None)
    plt.plot(all_rewards_dueling, marker='o', linewidth=5, linestyle='--', dashes=(5, 1), color='#2CBDFE')
    plt.subplot(324)
    plt.title('Dueling DQN: loss in comparable frames ', size=22, weight="bold")
    #plt.xlabel('Episode', size=22, weight="bold");
    plt.ylabel('Loss (Dueling DQN)', size=22, weight="bold");
    plt.xticks(size=20)
    plt.yticks(size=20)
    plt.ylim(0, 1200)
    plt.plot(losses_dueling, linewidth=3, color='#9D2EC5')
    plt.subplot(325)
    plt.title('Prioritised DQN: in frame %s, the reward is %s' % (update_interval, np.mean(all_rewards_prioritised[-10:])), size=22, weight="bold")
    plt.xlabel('Episode', size=22, weight="bold");
    plt.ylabel('Reward (Prioritised DQN)', size=22, weight="bold");
    plt.xticks(size=20)
    plt.yticks(size=20)
    plt.ylim(-400, 150)
    #plt.grid(b=None)
    plt.plot(all_rewards_prioritised, marker='o', linewidth=5, linestyle='--', dashes=(5, 5), color='#2CBDFE')
    plt.subplot(326)
    plt.title('Prioritised DQN: loss in comparable frames ', size=22, weight="bold")
    plt.xlabel('Episode', size=22, weight="bold");
    plt.ylabel('Loss (Prioritised DQN)', size=22, weight="bold");
    plt.xticks(size=20)
    plt.yticks(size=20)
    plt.ylim(0, 1200)
    plt.plot(losses_prioritised, linewidth=3, color='#9D2EC5')
    plt.tight_layout()
    plt.suptitle('Performance of Double, Dueling and Prioritised DQN on solving Lunar Lander problem', fontsize=40, weight="bold");
    plt.subplots_adjust(top=0.91)
    plt.show()

In [34]:
num_frames = 10000
batch_size = 32
gamma      = 0.99


losses_doubledqn = []
all_rewards_doubledqn = []
episode_reward_doubledqn = 0

losses_dueling = []
all_rewards_dueling = []
episode_reward_dueling = 0

losses_prioritised = []
all_rewards_prioritised = []
episode_reward_prioritised = 0

state_doubledqn = env.reset()
state_dueling = env.reset()
state_prioritised = env.reset()


for update_interval in range(1, num_frames + 1):
    epsilon_dueling = epsilon_by_frame_dueling(update_interval)
    epsilon_doubledqn = epsilon_by_frame_doubledqn(update_interval)
    epsilon_prioritised = epsilon_by_frame_prioritised(update_interval)
    
    action_doubledqn = current_model_doubledqn.act(state_doubledqn, epsilon_doubledqn)
    action_dueling = current_model_dueling.act(state_dueling, epsilon_dueling)
    action_prioritised = current_model_prioritised.act(state_prioritised, epsilon_prioritised)
    
    next_state_doubledqn, reward_doubledqn, terminal, _ = env.step(action_doubledqn)
    next_state_dueling, reward_dueling, terminal, _ = env.step(action_dueling)
    next_state_prioritised, reward_prioritised, terminal, _ = env.step(action_prioritised)

    replay_buffer_doubledqn.push(state_doubledqn, action_doubledqn, reward_doubledqn, next_state_doubledqn, terminal)
    replay_buffer_dueling.push(state_dueling, action_dueling, reward_dueling, next_state_dueling, terminal)
    replay_buffer_prioritised.push(state_prioritised, action_prioritised, reward_prioritised, next_state_prioritised, terminal)

    state_doubledqn= next_state_doubledqn   
    state_dueling = next_state_dueling
    state_prioritised = next_state_prioritised

    episode_reward_doubledqn += reward_doubledqn   
    episode_reward_dueling += reward_dueling
    episode_reward_prioritised += reward_prioritised

    
    if terminal:
        state_doubledqn = env.reset()
        state_dueling = env.reset()
        state_prioritised = env.reset()
        
        all_rewards_doubledqn.append(episode_reward_doubledqn)
        all_rewards_dueling.append(episode_reward_dueling)
        all_rewards_prioritised.append(episode_reward_prioritised)

        episode_reward_doubledqn = 0        
        episode_reward_dueling = 0
        episode_reward_prioritised = 0

    if len(replay_buffer_doubledqn) > batch_size:
        loss_doubledqn = td_loss_doubledqn(batch_size)
        losses_doubledqn.append(loss_doubledqn.item())
        
    if len(replay_buffer_dueling) > batch_size:
        loss_dueling = td_loss_dueling(batch_size)
        losses_dueling.append(loss_dueling.item())
    
    if len(replay_buffer_prioritised) > batch_size:
        beta = beta_by_frame(update_interval)
        loss_prioritised = td_loss_prioritised(batch_size, beta)
        losses_prioritised.append(loss_prioritised.item())
        
    if update_interval % 200 == 0:
        plot_dynamic(update_interval, np.round(all_rewards_doubledqn,2), losses_doubledqn)
        plot_dynamic(update_interval, np.round(all_rewards_dueling,2), losses_dueling)
        plot_dynamic(update_interval, np.round(all_rewards_prioritised,2), losses_prioritised) 

        
    if update_interval % 100 == 0:
        update_target_doubledqn(current_model_doubledqn, target_model_doubledqn)
        update_target_dueling(current_model_dueling, target_model_dueling)
        update_target_prioritised(current_model_prioritised, target_model_prioritised)


In [35]:
plt.savefig("Task4.svg")

<Figure size 1800x1200 with 0 Axes>